Sử dụng thuật toán di truyền để tìm trọng số cho mạng nơ ron tế bào cho bài toán tìm biên ảnh.
Một số lưu ý trong quá trình code:
- Do hàm giải phương trình vi phân (ODE) chỉ nhận mảng 1 chiều (array) vào giá trị ban đầu cũng như đầu ra của x nên phải biến đổi từ dạng ma trận về mảng 1 chiều ở một số phép tính.
- Thứ tự của m, n (kích thước của ma trận đầu vào) đôi khi bị ngược nhau trong quá trình reshape. Lưu ý khi đưa vào ma trận không vuông.
- Các số dùng trong phép tính nên để ở dạng float

In [1]:
from scipy.signal import convolve2d
from scipy.integrate import ode
from PIL import Image as img
import numpy as np
import numpy.matlib as mat
import math

In [5]:
# hàm trạng thái
def hamTrangThai(t, x, u, B, A, I, n, m):
    x = x.reshape(n, m)
    dx = -x + convolve2d(u, B, 'same') + convolve2d(hamDauRa(x), A, 'same') + I
    return dx.reshape(n*m)

# hàm đầu ra
def hamDauRa(x):
    return 0.5 * (abs(x + 1) - abs(x - 1))

# Tạo ma trận đối xứng từ 5 trọng số (hàm này chỉ dành riêng cho ma trận đối xứng 3x3)
def taoMaTranDoiXung(arr1):#giả sử cho mảng [1,2,3,4,5]
    arr2 = arr1[-2::-1].copy()#tạo mảng phụ [4,3,2,1]
    arr2[0], arr2[2] = arr2[2], arr2[0]#nếu không có lệnh này thì ma trận tạo ra sẽ bị ngược
    return np.append(arr1,arr2).reshape(h,h)#kết hợp hai mảng rồi chuyển về dạng ma trận 3x3

# Hàm lai hai số
def lai(a,b):#k là điểm lai  -3,|45
    if(a>0):
        return math.modf(a)[1]+abs(math.modf(b)[0])
    return math.modf(a)[1]-abs(math.modf(b)[0])

# Hàm tạo số ngẫu nhiên từ -9.99 đến 9.99
def ngauNhien():
    return np.random.randint(-999,1000)/100.

# Hàm tính sai số
def saiSo(d,y):
    return np.sum(0.5*(d-y)**2)

# Quần thể trọng số (gồm 11 số)
quanThe = np.array([ngauNhien() for i in range(11)])

# kích thước ma trận đầu vào, ma trận đầu ra và ma trận trạng thái
m, n = 4, 4

# ma trận ảnh đầu vào u
u = np.array([
    [ 1, 1, 1, 1],
    [ 1, 1, 1, 1],
    [ 1, 1, 1, 1],
    [ 1, 1, 1, 1]], dtype=float)

# ma trận đầu ra mong muốn d
d = np.array([
    [ 1, 1, 1, 1],
    [ 1,-1,-1, 1],
    [ 1,-1,-1, 1],
    [ 1, 1, 1, 1]], dtype=float)

# Bán kính lân cận của nơ ron tế bào
r = 1

# kích thước của ma trận điều khiển và ma trận phản hồi (hai ma trận này luôn vuông)
h = 2*r + 1

# ma trận điều khiển B ban đầu
# B = np.array([
#     [-1.,-1.,-1.],
#     [-1., 8.,-1.],
#     [-1.,-1.,-1.]])
B = taoMaTranDoiXung(quanThe[:5])

# ma trận phản hồi A ban đầu
# A = np.array([
#     [ 0., 0., 0.],
#     [ 0., 1., 0.],
#     [ 0., 0., 0.]])
A = taoMaTranDoiXung(quanThe[5:10])

# mức ngưỡng I ban đầu
I = quanThe[10]
#I = -1.0

# sai số cho phép
E0 = 2.0

# hai giá trị ban đầu cho x với t0 = 0 và t để tính đầu ra x (t != t0)
x, t = u, 0.5

# ma trận đầu ra ban đầu
y = hamDauRa(x)

# khởi tạo phương trình vi phân
ptvp = ode(hamTrangThai) 
ptvp.set_integrator('vode')
ptvp.set_initial_value(x.flatten(), 0.0) 

print(f'A = {A}')
print(f'B = {B}')
print(f'x = {x}')
print(f'd = {d}')

A = [[ 7.97  1.56 -7.81]
 [ 0.7   7.65  1.56]
 [-7.81  0.7   7.97]]
B = [[9.74 6.3  1.19]
 [1.38 9.54 6.3 ]
 [1.19 1.38 9.74]]
x = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
d = [[ 1.  1.  1.  1.]
 [ 1. -1. -1.  1.]
 [ 1. -1. -1.  1.]
 [ 1.  1.  1.  1.]]


In [6]:
#Tìm trọng số
Etruoc = 1000000000 # sai số của lần tính trước đó
S = 50 # số cha mẹ được chọn để lai mới mỗi trọng số 
loop = 1000 #số lần chạy thử tối đa
count = 0 # số lần chạy
while(ptvp.successful() and Etruoc>E0 and count<loop):
    # đếm số lần chạy
    count+=1
    print(f'Lần chạy thứ {count}')

    # xét trọng số
    tsl = count%11 # STT trọng số hiện tại đang được lai (trọng số lai)
    #print(f'xét trọng số thứ {tsl} trong quần thể')
    tapChaMe = [[ngauNhien(),ngauNhien()] for i in range(S)]
    #print(f'Tập cha mẹ: {}')
    for chaMe in tapChaMe:
        #print(f'Tạo trọng số con thứ {i+1}:')
        trongSoMoi = lai(chaMe[0],chaMe[1])
        #print(f'Trọng số mới: {trongSoMoi}')
        trongSoCu = quanThe[tsl]
        quanThe[tsl] = trongSoMoi
        A = taoMaTranDoiXung(quanThe[:5])
        #print(f'A = {A}')
        B = taoMaTranDoiXung(quanThe[5:10])
        #print(f'B = {B}')
        I = quanThe[10]
        #print(f'I = {I}')
        ptvp.set_initial_value(x.flatten(), 0.0)
        #u = x.copy()
        ptvp.set_f_params(u, B, A, I, n, m)
        x = (ptvp.integrate(t))[:].reshape(n, m)
        #print(f'x = {x}')
        
        y = hamDauRa(x)
        print(f'y = {y}')
        E = saiSo(d,y)
        if(E>Etruoc):
            quanThe[tsl] = trongSoCu
        else:
            Etruoc = E
    print(f'Kết quả: E = {Etruoc}')
    

Lần chạy thứ 1
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]
 [1. 1. 1. 1.]]
y = [[1. 1

Test các hàm

In [7]:
ptvp.set_f_params(u, B, A, I, n, m)
assert ptvp.successful()
x = (ptvp.integrate(t))[:].reshape(n, m)
y = hamDauRa(x)
y

array([[1., 1., 1., 1.],
       [1., 1., 1., 1.],
       [1., 1., 1., 1.],
       [1., 1., 1., 1.]])

In [5]:
taoMaTranDoiXung([1,2,3,4,5])
taoMaTranDoiXung(quanThe[:5])

array([[8.64, 6.14, 7.53],
       [8.93, 8.06, 6.14],
       [7.53, 8.93, 8.64]])

In [8]:
saiSo(d,y)

0.01

In [260]:
# khởi tạo phương trình vi phân
ptvp = ode(hamTrangThai) \
.set_integrator('vode') \
.set_initial_value(x.flatten(), 0.0) \
.set_f_params(u, B, A, I, n, m)
assert ptvp.successful()
x = ptvp.integrate(t)
y = hamDauRa(x[:].reshape(n, m))
y

array([[ 1.        ,  1.        ,  1.        ,  1.        ],
       [ 1.        ,  1.        , -1.        ,  1.        ],
       [-1.        ,  1.        ,  1.        ,  1.        ],
       [-0.79406178, -1.        ,  1.        ,  1.        ]])

In [147]:
lai(-2.04,-8.74)

-2.74

In [98]:
ngauNhien()

-8.62

In [144]:
c = 3.22
math.modf(c)

(0.2200000000000002, 3.0)

In [259]:
print(A,B,I)

[[-1.83  9.66 -2.24]
 [-9.74  2.76  9.66]
 [-2.24 -9.74 -1.83]] [[ 1.38 -2.55  2.  ]
 [-5.19  8.23 -2.55]
 [ 2.   -5.19  1.38]] 6.34
